# Import CSV files, combine them and extract Numpy arrays

In [ ]:
import numpy as np
import pandas as pd
import json
import os
import glob
import re
from ast import literal_eval

: 

: 

### Import files into pd.DataFrame

In [ ]:
dname = os.getcwd() + '/data_v2/'
dname

'c:\\Users\\Jirko\\Desktop\\Hip_Lab\\analysis_scripts\\data_loading/data_v2/'

In [ ]:
# list the file names
fnames = glob.glob(dname + '*.txt')
fnames

In [9]:
# regular expressions to make the file suitable to be read into a dataframe
def replace_several(diction, text):
    # create regex from dict
    regex = re.compile("(%s)" % "|".join(map(re.escape, diction.keys())))

    # look-up value in dictionary
    return regex.sub(lambda mo: diction[mo.string[mo.start():mo.end()]], text)  

# dictionary for replacement
expres_dict = {"sdata": '\"sdata\"', "edata": '\"edata\"', "parameters": '\"parameters\"'}

# run a loop over file names
for fname in fnames:
    # make a new file to place the data
    newfile = open("data_v2_quotes/"+ os.path.basename(os.path.normpath(fname)) , 'w')
    # print("data_v2_quotes/"+ os.path.basename(os.path.normpath(fname)))
    for i, line in enumerate(open(fname)):
        rep_line = replace_several(expres_dict, line)
        # replace the content of the file line by line
        newfile.write("%s" % rep_line)
        # newfile.write('\n')

In [7]:
#  function from https://github.com/aranas
def data2dict(file_path):
    """ Load in data saved from javascript online study
    Deals with missing '{}' and outputs data in the form of dicts.
    ​
    Parameters:
    path_to_file (str) : full path to file that contains data
​   
    Returns:
    out (list) : list of dicts from file
    ​
    """
    with open(file_path, "r") as file:
        data_read = file.read().split('\n')
    out = [json.loads('{' + line + '}') for line in data_read]
    return out

# test = data2dict("data_v2_quotes/3dWkc3IGEK2s.txt")
# print(len(test))
# print(test[])


In [ ]:
dname_new = os.getcwd() + '/data_v2_quotes/'
fnames_new = glob.glob(dname_new + '*.txt')
print(fnames_new)

In [12]:
DF = pd.DataFrame()
for i, fname in enumerate(fnames):

    with open(fname) as f:
        # read the data and transform to a dictionary
        data = f.read() 
        js = json.loads(data)
        print(len(js["sdata"]))
        # enter the dict into a dataframe
        df = pd.DataFrame.from_dict(js["sdata"], orient='index')
        df = df.transpose() # small hack to load data into dataframe
        # add a participant ID
        df.insert(loc=0, column="id", value=i)
    
    # Append to the big dataFrame
    DF = DF.append(df, ignore_index=True)

JSONDecodeError: Expecting value: line 1 column 1 (char 0)

In [24]:
def create_df(fnames, data_type, dict_idx):
    """function to create the dataframe from the files"""
    DF = pd.DataFrame()
    for i, fname in enumerate(fnames[:-1]):
        list_of_dicts = data2dict(fname)
        # get the relevant sdata
        data_dict = list_of_dicts[dict_idx][data_type]
        
        # remove entries of type integer
        for key in list(data_dict):
            if isinstance(data_dict[key], int):
                del data_dict[key]

        # creating the dict
        df = pd.DataFrame.from_dict(data_dict, orient='index')
        df = df.transpose() # small hack to load data into dataframe
        # add a participant ID
        df.insert(loc=0, column="id", value=i)
    
        # Append to the big dataFrame
        DF = DF.append(df, ignore_index=True)
    return DF 

# DF = create_df(fnames_new, "sdata")


Creating an dataframe for the edata to count gender and age

In [ ]:
# create the dataframe
df_edata = create_df(fnames_new, "edata", 1)

df_edata


In [27]:
# count peoples gender
df_edata['expt_sex'].value_counts()

female    33
male      13
other      2
Name: expt_sex, dtype: int64

### Explore DataFrame

In [21]:
pd.set_option('display.max_columns', None)
# DF.drop(columns=["trial_bonus", "block_bonus", "resp_indices", "resp_indices_values", "resp_timestamp", "resp_reactiontime"], inplace=True)
DF.shape
DF.head(3)

id expt_index expt_trial expt_block trial_att vbxi_category exemplar  \
0   0          0          0          0         1             7       10   
1   0          1          1          0         0             7        0   
2   0          2          2          0         1             3        1   

         trialProperties                                  trialPropShuff  \
0  [1, 0, 1, 0, 0, 0, 1]  [[0, 1, 0, 0, 1, 0, 1], [0, 0, 0, 1, 1, 1, 0]]   
1  [1, 0, 1, 0, 0, 0, 1]                         [[1, 1, 1, 0, 0, 0, 0]]   
2  [1, 1, 0, 0, 1, 0, 0]  [[1, 0, 0, 0, 1, 0, 1], [1, 1, 1, 0, 0, 0, 0]]   

  trial_bonus block_bonus                  resp_timestamp resp_reactiontime  \
0           1          23  [1656927914973, 1656927926827]   [9.699, 21.552]   
1           3          32                 [1656927934679]           [5.846]   
2           1          31  [1656927943664, 1656927953941]   [6.981, 17.258]   

                                   property_order  \
0  [[1, 0, 5, 4, 2, 3, 6], [5, 3, 4, 2, 0, 6, 1]]   
1                         [[0, 6, 2, 3, 1, 5, 4]]   
2  [[4, 2, 5, 3, 1, 6, 0], [0, 4, 1, 2, 5, 3, 6]]   

                                  resp_correct_array  \
0  [[False, True, False, None, None, None, None],...   
1       [[True, True, True, None, None, None, None]]   
2  [[None, None, False, False, True, None, None],...   

                           resp_correct_array_unshuf  \
0  [[True, False, None, None, None, False, None],...   
1       [[True, None, True, None, None, None, True]]   
2  [[None, True, None, False, None, False, None],...   

                                      prop_responses  \
0  [[1, 1, 1, None, None, None, None], [None, Non...   
1                [[1, 1, 1, None, None, None, None]]   
2  [[None, None, 1, 1, 1, None, None], [1, 1, 1, ...   

                               groundTruthCorrect  \
0  [[0, 1, 0, 1, 0, 1, 0], [1, 1, 1, 1, 1, 1, 1]]   
1                         [[1, 1, 1, 1, 1, 1, 1]]   
2  [[0, 1, 0, 0, 1, 1, 0], [1, 1, 1, 1, 1, 1, 1]]   

                        groundTruthCorrect_unshuf            resp_indices  \
0  [[1, 0, 0, 1, 1, 0, 0], [1, 1, 1, 1, 1, 1, 1]]  [[0, 2, 1], [4, 3, 5]]   
1                         [[1, 1, 1, 1, 1, 1, 1]]             [[0, 1, 2]]   
2  [[0, 1, 1, 0, 0, 0, 1], [1, 1, 1, 1, 1, 1, 1]]  [[2, 4, 3], [1, 2, 0]]   

      resp_indices_values  
0  [[1, 1, 1], [1, 1, 1]]  
1             [[1, 1, 1]]  
2  [[1, 1, 1], [1, 1, 1]]

### Filter responses

In [22]:
# drop redundant columns
# DF.drop(columns=["relevProps", "relevPropsShuff"], inplace=True)
DF.head(3)

id expt_index expt_trial expt_block trial_att vbxi_category exemplar  \
0   0          0          0          0         1             7       10   
1   0          1          1          0         0             7        0   
2   0          2          2          0         1             3        1   

         trialProperties                                  trialPropShuff  \
0  [1, 0, 1, 0, 0, 0, 1]  [[0, 1, 0, 0, 1, 0, 1], [0, 0, 0, 1, 1, 1, 0]]   
1  [1, 0, 1, 0, 0, 0, 1]                         [[1, 1, 1, 0, 0, 0, 0]]   
2  [1, 1, 0, 0, 1, 0, 0]  [[1, 0, 0, 0, 1, 0, 1], [1, 1, 1, 0, 0, 0, 0]]   

  trial_bonus block_bonus                  resp_timestamp resp_reactiontime  \
0           1          23  [1656927914973, 1656927926827]   [9.699, 21.552]   
1           3          32                 [1656927934679]           [5.846]   
2           1          31  [1656927943664, 1656927953941]   [6.981, 17.258]   

                                   property_order  \
0  [[1, 0, 5, 4, 2, 3, 6], [5, 3, 4, 2, 0, 6, 1]]   
1                         [[0, 6, 2, 3, 1, 5, 4]]   
2  [[4, 2, 5, 3, 1, 6, 0], [0, 4, 1, 2, 5, 3, 6]]   

                                  resp_correct_array  \
0  [[False, True, False, None, None, None, None],...   
1       [[True, True, True, None, None, None, None]]   
2  [[None, None, False, False, True, None, None],...   

                           resp_correct_array_unshuf  \
0  [[True, False, None, None, None, False, None],...   
1       [[True, None, True, None, None, None, True]]   
2  [[None, True, None, False, None, False, None],...   

                                      prop_responses  \
0  [[1, 1, 1, None, None, None, None], [None, Non...   
1                [[1, 1, 1, None, None, None, None]]   
2  [[None, None, 1, 1, 1, None, None], [1, 1, 1, ...   

                               groundTruthCorrect  \
0  [[0, 1, 0, 1, 0, 1, 0], [1, 1, 1, 1, 1, 1, 1]]   
1                         [[1, 1, 1, 1, 1, 1, 1]]   
2  [[0, 1, 0, 0, 1, 1, 0], [1, 1, 1, 1, 1, 1, 1]]   

                        groundTruthCorrect_unshuf            resp_indices  \
0  [[1, 0, 0, 1, 1, 0, 0], [1, 1, 1, 1, 1, 1, 1]]  [[0, 2, 1], [4, 3, 5]]   
1                         [[1, 1, 1, 1, 1, 1, 1]]             [[0, 1, 2]]   
2  [[0, 1, 1, 0, 0, 0, 1], [1, 1, 1, 1, 1, 1, 1]]  [[2, 4, 3], [1, 2, 0]]   

      resp_indices_values  
0  [[1, 1, 1], [1, 1, 1]]  
1             [[1, 1, 1]]  
2  [[1, 1, 1], [1, 1, 1]]

### Save full DataFrame to CSV

In [91]:
DF.to_csv(dname_new + 'full_data.csv')

### Retreive parameters

In [16]:
sujs = DF['id'].unique()
n_sujs = sujs.size
n_sujs

49

In [19]:
n_trials_per_suj = DF.loc[DF['id'] == sujs[0]].shape[0]
n_trials_per_suj

128

In [94]:
n_blocs = DF['expt_block'].unique().size
n_blocs

8

In [95]:
n_trials_per_block = int(n_trials_per_suj/n_blocs)
n_trials_per_block

16

### Put data in numpy arrays

In [99]:
ACCURACY = np.full((n_sujs, n_blocs, n_trials_per_block), np.nan)
acc_first_prop = np.full((n_sujs, n_blocs, n_trials_per_block), np.nan)
acc_second_prop = np.full((n_sujs, n_blocs, n_trials_per_block), np.nan)
acc_third_prop = np.full((n_sujs, n_blocs, n_trials_per_block), np.nan)
# RT = np.full((n_sujs, n_blocs, n_trial), np.nan)
# BLOC_TYPE = np.full((n_sujs, n_blocs), np.nan, dtype=np.object)

# Loop across participant and blocs
for i, suj in enumerate(sujs):
    for block in range(n_blocs):

        # Select lines in the DataFrame
        _DF = DF.loc[(DF['id'] == suj) & (DF['expt_block'] == block)]

        _DF["Correct"] = _DF["resp_correct_array_unshuf"].apply(lambda x: np.asarray(x)[0])
        _DF["Correct"] = _DF["Correct"].apply(lambda x: np.select([x == True],[1]))

        # Accuracy
        ACCURACY[i, block, :_DF.shape[0]] = _DF["Correct"].apply(lambda x: np.sum(x)/3)
        # accuracy on first property
        acc_first_prop[i, block, :_DF.shape[0]] = _DF["Correct"].apply(lambda x: np.sum(x[0]))
        
        # accuracy on second property
        acc_second_prop[i, block, :_DF.shape[0]] = _DF["Correct"].apply(lambda x: np.sum(x[1:3]))
        # accuracy on second property
        acc_third_prop[i, block, :_DF.shape[0]] = _DF["Correct"].apply(lambda x: np.sum(x[3:]))
        # Reaction times
        # RT[i, j, :_DF.shape[0]] = _DF['data : "rt"']
        
        # Bloc type
        # BLOC_TYPE[i, j] = _DF['bloc_type'].unique()[0]

C:\Users\Jirko\AppData\Local\Temp\ipykernel_15220\972292794.py:15: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  _DF["Correct"] = _DF["resp_correct_array_unshuf"].apply(lambda x: np.asarray(x)[0])
C:\Users\Jirko\AppData\Local\Temp\ipykernel_15220\972292794.py:16: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  _DF["Correct"] = _DF["Correct"].apply(lambda x: np.select([x == True],[1]))
C:\Users\Jirko\AppData\Local\Temp\ipykernel_15220\972292794.py:15: SettingWithCopyWarning: 
A value is trying to be set on a c

### Save data as numpy arrays

In [100]:
np.save(dname_new + 'ACCURACY_New.npy', ACCURACY)
np.save(dname_new + 'Acc_first_prop_New.npy', acc_first_prop)
np.save(dname_new + 'acc_second_prop_New.npy', acc_second_prop)
np.save(dname_new + 'acc_third_prop_New.npy', acc_third_prop)
# np.save(dname + 'SUJS.npy', sujs)

Make a new numpy arrays to store trial-wise accuracy

In [30]:
ACCURACY_trials = np.full((n_sujs, n_trials_per_suj), np.nan)
acc_first_prop_trials = np.full((n_sujs, n_trials_per_suj), np.nan)
acc_second_prop_trials = np.full((n_sujs, n_trials_per_suj), np.nan)
acc_third_prop_trials = np.full((n_sujs, n_trials_per_suj), np.nan)

# Loop across participant and trials
for i, suj in enumerate(sujs):
    for j, trial in enumerate(range(n_trials_per_suj)):

        # Select lines in the DataFrame
        _DF = DF.loc[(DF['id'] == suj) & (DF['expt_index'] == trial)]

        _DF["Correct"] = _DF["resp_correct_array_unshuf"].apply(lambda x: np.asarray(x)[0])
        _DF["Correct"] = _DF["Correct"].apply(lambda x: np.select([x == True],[1]))

        # Accuracy
        ACCURACY_trials[i, j] = _DF["Correct"].apply(lambda x: np.sum(x)/3)
        # accuracy on first property
        acc_first_prop_trials[i, j] = _DF["Correct"].apply(lambda x: np.sum(x[0]))
        
        # accuracy on second property
        acc_second_prop_trials[i, j] = _DF["Correct"].apply(lambda x: np.sum(x[1:3]))
        # accuracy on second property
        acc_third_prop_trials[i, j] = _DF["Correct"].apply(lambda x: np.sum(x[3:]))
    print(i)

ACCURACY_trials.shape

C:\Users\Jirko\AppData\Local\Temp\ipykernel_14296\2800615808.py:13: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  _DF["Correct"] = _DF["resp_correct_array_unshuf"].apply(lambda x: np.asarray(x)[0])
C:\Users\Jirko\AppData\Local\Temp\ipykernel_14296\2800615808.py:14: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  _DF["Correct"] = _DF["Correct"].apply(lambda x: np.select([x == True],[1]))
C:\Users\Jirko\AppData\Local\Temp\ipykernel_14296\2800615808.py:13: SettingWithCopyWarning: 
A value is trying to be set on 

0


C:\Users\Jirko\AppData\Local\Temp\ipykernel_14296\2800615808.py:13: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  _DF["Correct"] = _DF["resp_correct_array_unshuf"].apply(lambda x: np.asarray(x)[0])
C:\Users\Jirko\AppData\Local\Temp\ipykernel_14296\2800615808.py:14: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  _DF["Correct"] = _DF["Correct"].apply(lambda x: np.select([x == True],[1]))
C:\Users\Jirko\AppData\Local\Temp\ipykernel_14296\2800615808.py:13: SettingWithCopyWarning: 
A value is trying to be set on 

1


C:\Users\Jirko\AppData\Local\Temp\ipykernel_14296\2800615808.py:14: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  _DF["Correct"] = _DF["Correct"].apply(lambda x: np.select([x == True],[1]))
C:\Users\Jirko\AppData\Local\Temp\ipykernel_14296\2800615808.py:13: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  _DF["Correct"] = _DF["resp_correct_array_unshuf"].apply(lambda x: np.asarray(x)[0])
C:\Users\Jirko\AppData\Local\Temp\ipykernel_14296\2800615808.py:14: SettingWithCopyWarning: 
A value is trying to be set on 

...

47


C:\Users\Jirko\AppData\Local\Temp\ipykernel_14296\2800615808.py:14: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  _DF["Correct"] = _DF["Correct"].apply(lambda x: np.select([x == True],[1]))
C:\Users\Jirko\AppData\Local\Temp\ipykernel_14296\2800615808.py:13: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  _DF["Correct"] = _DF["resp_correct_array_unshuf"].apply(lambda x: np.asarray(x)[0])
C:\Users\Jirko\AppData\Local\Temp\ipykernel_14296\2800615808.py:14: SettingWithCopyWarning: 
A value is trying to be set on 

48


C:\Users\Jirko\AppData\Local\Temp\ipykernel_14296\2800615808.py:14: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  _DF["Correct"] = _DF["Correct"].apply(lambda x: np.select([x == True],[1]))
C:\Users\Jirko\AppData\Local\Temp\ipykernel_14296\2800615808.py:13: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  _DF["Correct"] = _DF["resp_correct_array_unshuf"].apply(lambda x: np.asarray(x)[0])
C:\Users\Jirko\AppData\Local\Temp\ipykernel_14296\2800615808.py:14: SettingWithCopyWarning: 
A value is trying to be set on 

(49, 128)

In [31]:
np.save(dname_new + 'ACCURACY_New_trials.npy', ACCURACY_trials)
np.save(dname_new + 'Acc_first_prop_New_trials.npy', acc_first_prop_trials)
np.save(dname_new + 'acc_second_prop_New_trials.npy', acc_second_prop_trials)
np.save(dname_new + 'acc_third_prop_New_trials.npy', acc_third_prop_trials)
acc_second_prop_trials.shape

(49, 128)